In [2]:
import pandas as pd 
import numpy as np
from bertopic import BERTopic

#load data 
import pandas as pd 
 
df = pd.read_csv("./data.csv", engine='python',sep='^')
#df = df.astype(str)
docs= []
valueList = df.values.tolist()
for value in valueList:
    docs.append(value[0])

#print(docs)
#df['nova_descricao'] = df['nova_descricao'].str.replace('[,.:;!?]+', ' ', regex=True).copy()
#df['nova_descricao'] = df['nova_descricao'].str.replace ('[/<>()|\+\-\$%&#@\'\"]+', ' ', regex=True).copy()
#df['nova_descricao'] = df['nova_descricao'].str.replace('[0-9]+', '', regex=True).copy()


In [3]:
# create model 
 
from sklearn.feature_extraction.text import CountVectorizer
from nltk.corpus import stopwords 
pt_stopwords = stopwords.words('portuguese')


# we add this to remove stopwords
vectorizer_model = CountVectorizer(strip_accents='ascii',ngram_range=(1, 2), stop_words=pt_stopwords)

model = BERTopic(
    vectorizer_model=vectorizer_model,
    language='portuguese', calculate_probabilities=True,
    verbose=True
)

#convert to list 
#docs = df.values.tolist()
 
topics, probabilities = model.fit_transform(docs)


Batches: 100%|██████████| 79/79 [01:38<00:00,  1.24s/it]
2023-02-13 09:32:02,651 - BERTopic - Transformed documents to Embeddings
2023-02-13 09:32:28,059 - BERTopic - Reduced dimensionality
2023-02-13 09:32:29,063 - BERTopic - Clustered reduced embeddings


In [4]:
model.get_topic_freq().head(11)

Topic  Count
0      -1    919
1       0     80
2       1     54
3       2     53
4       3     48
5       4     46
6       5     43
7       6     43
8       7     43
9       8     41
10      9     40

In [5]:
model.get_topic(0)

[('congresso nacional', 0.042529751032631624),
 ('congresso', 0.04237054724127585),
 ('dias', 0.03484887115531616),
 ('nacional', 0.031198580977646242),
 ('prazo', 0.022191482093572572),
 ('sessao', 0.020129678267579956),
 ('projeto', 0.01884078711589038),
 ('sessao legislativa', 0.017153113584140168),
 ('ate', 0.017140149336685607),
 ('legislativa', 0.016194365317740045)]

In [6]:
model.get_topic_info()

Topic  Count                                               Name
0      -1    919                            -1_federal_1988_br_span
1       0     80       0_congresso nacional_congresso_dias_nacional
2       1     54       1_presidente_senado federal_senado_deputados
3       2     53  2_orcamentarias_diretrizes orcamentarias_diret...
4       3     48            3_cargo_emprego_trabalho_emprego funcao
..    ...    ...                                                ...
59     58     11              58_petroleo_derivados_gas_gas natural
60     59     10  59_cidadania_cidadania direitos_politicos_naci...
61     60     10            60_direitos_pessoa_humana_pessoa humana
62     61     10         61_dados_dados pessoais_pessoais_registros
63     62     10  62_uniao_inclusive compartilhamento_informacoe...

[64 rows x 3 columns]

In [7]:
model.visualize_topics()


In [8]:
model.visualize_barchart()


In [9]:
model.visualize_heatmap()


In [10]:
from scipy.cluster import hierarchy as sch
# Hierarchical topics
linkage_function = lambda x: sch.linkage(x, 'single', optimal_ordering=True)
hierarchical_topics = model.hierarchical_topics(docs, linkage_function=linkage_function)
model.visualize_hierarchy(hierarchical_topics=hierarchical_topics)

100%|██████████| 62/62 [00:00<00:00, 62.27it/s]


In [11]:
tree = model.get_topic_tree(hierarchical_topics)
print(tree)

.
├─■──desde_juntas comerciais_obito natos_vedados sao_consorcios sorteios ── Topic: 22
└─federal_span_br_1988_lei
     ├─federal_span_br_1988_lei
     │    ├─■──dados_dados pessoais_pessoais_registros_protecao ── Topic: 61
     │    └─federal_span_br_1988_lei
     │         ├─federal_span_br_1988_lei
     │         │    ├─federal_span_br_1988_lei
     │         │    │    ├─federal_span_br_1988_constituicao
     │         │    │    │    ├─span_federal_br_1988_constituicao
     │         │    │    │    │    ├─■──transporte_ilhas_fluviais_transportes_dominio ── Topic: 27
     │         │    │    │    │    └─span_federal_br_1988_constituicao
     │         │    │    │    │         ├─■──deficiencia_protecao_atendimento_adolescente_especializado ── Topic: 28
     │         │    │    │    │         └─span_federal_br_1988_constituicao
     │         │    │    │    │              ├─span_federal_br_1988_constituicao
     │         │    │    │    │              │    ├─cultura_desenvolvimento_cul

In [12]:

from sentence_transformers import SentenceTransformer

sentence_model = SentenceTransformer("paraphrase-multilingual-MiniLM-L12-v2")
embeddings = sentence_model.encode(docs, show_progress_bar=False)


model.visualize_hierarchical_documents(docs, hierarchical_topics, embeddings=embeddings)



In [13]:
from umap import UMAP
reduced_embeddings = UMAP(n_neighbors=10, n_components=2, min_dist=0.0, metric='cosine').fit_transform(embeddings)
model.visualize_hierarchical_documents(docs, hierarchical_topics, reduced_embeddings=reduced_embeddings)